### Import Packages

In [1]:
from datetime import datetime
import pandas as pd 
import numpy as np
from random import randrange
from tqdm import *
import plotly.express as px
import requests

import plotly.graph_objects as go
from plotly.subplots import make_subplots
from importData import *

In [14]:
futurePriceDict = np.load('futurePriceDict.npy',allow_pickle='TRUE').item()

In [15]:
futurePriceDict[pd.Timestamp(2024,4,1)]['BTC']

timestamp     open     high      low    close        volume  \
0    1.704067e+09  42313.9  42832.0  42270.0  42369.8  1.287748e+09   
1    1.704082e+09  42369.8  42536.0  42207.9  42527.0  8.002889e+08   
2    1.704096e+09  42527.1  42800.0  42489.4  42727.6  9.058092e+08   
3    1.704110e+09  42727.7  42887.5  42614.5  42818.0  9.897540e+08   
4    1.704125e+09  42818.3  43593.2  42693.1  43556.2  2.004709e+09   
..            ...      ...      ...      ...      ...           ...   
633  1.713182e+09  65848.6  66369.7  63800.0  64545.8  6.180509e+09   
634  1.713197e+09  64552.6  64848.8  62242.5  63269.9  7.223517e+09   
635  1.713211e+09  63270.0  63610.3  62606.0  63392.7  2.694956e+09   
636  1.713226e+09  63392.8  63879.6  62711.0  62937.6  2.763541e+09   
637  1.713240e+09  62937.6  63786.3  61651.8  63487.9  4.295293e+09   

              open_time token  
0   2024-01-01 00:00:00   BTC  
1   2024-01-01 04:00:00   BTC  
2   2024-01-01 08:00:00   BTC  
3   2024-01-01 12:00:00   BTC  
4   2024-01-01 16:00:00   BTC  
..                  ...   ...  
633 2024-04-15 12:00:00   BTC  
634 2024-04-15 16:00:00   BTC  
635 2024-04-15 20:00:00   BTC  
636 2024-04-16 00:00:00   BTC  
637 2024-04-16 04:00:00   BTC  

[638 rows x 8 columns]

### Get Data from Binance API

In [2]:
from binance_api import *
from datetime import datetime


# tokensAI = [ "AR", "FET" , "ARKM" , "OCEAN", "WLD", "AI", "AGIX", "TAO","RNDR","AKT","FET",
#             "CORGIAI","AGIX","OLAS", "OCEAN","TRAC","PRIME","GLM","RLC","AIOZ","NMR", 
#             "ARKM","SURE","ORAI","IQ","PAAL","RSS3","AGRS","ALI","ZIG",
#             "ALEPH","CGPT","DNX","ARC","HEART","LMWR"]

tokensAI = ["AGIX","AI","AR","ARKM","CTXC","FET","GRT","IQ","LPT","MDT","NEAR","NFP","OCEAN","PHA","PHB","RNDR","THETA","WLD"]

# tokensGameFi = [ "MBOX", "BEAMX" , "ARKM" , "RONIN" , "ICP","IMX","SAND","AXS","BEAM",
#                  "APE","GALA","RON","ILV","GMT","ENJ","MAGIC","FLOKI","PRIME","WAXP","OAS","PYR",
#                  "YGG","BLZ","SLP","HOOK","NAKA","ALICE","WILD","GF","MC","POLIS","SWEAT","SHRAP","GOG"]


tokensGameFi = ["ACE","APE","AXS","BEAMX","BURGER","CHR",
                "COMBO","DAR","ENJ","FLOW","GALA","GHST","GMT",
                "HIGH","ILV","IMX","MAGIC","MANA","MBOX","PDA",
                "PIXEL","PORTAL","PYR","RONIN","SAND","SLP",
                "SUPER","TLM","VOXEL","XAI","YGG"]



tokensDict= {
    'AI' : tokensAI,
    'GameFi' : tokensGameFi,
}
         

In [14]:
def get_rank_data(year, month, day):

    req = requests.get(f'http://192.168.1.140:8001/coingecko/historical_100_coins?year={year}&month={month}&day={day}')
    return req.json()

In [15]:
startDate = pd.Timestamp(2020,1,1)
tokensTop100 = {}

while startDate <=  pd.Timestamp(2024,3,1) : 
    
    marketCapDate = startDate - pd.DateOffset(days = 1)
    
    year = marketCapDate.year
    month = marketCapDate.month
    day = marketCapDate.day

    rankDict = get_rank_data(year,month,day)
    rankDf = pd.json_normalize(rankDict)

    tokensTop100[startDate] = rankDf['symbol'].array

    startDate = startDate + pd.DateOffset(months = 3)


In [8]:
# df_kbar = {}

# for date, symbols in tokensTop100.items() : 

#     df_kbar[date] = {}

#     for symbol in symbols : 
#         print("Now Downloading : " + symbol)
        
#         try : 
#             df_kbar[date][symbol] = get_klines_data_from_binance(symbol= symbol + "USDT", 
#                                                                    resample_freq ='4h', 
#                                                                    start_time = date - pd.DateOffset(months = 3), 
#                                                                    end_time = date + pd.DateOffset(months = 3), 
#                                                                    futures=False)
#         except : 
#             pass

# np.save('top100Kbar.npy', df_kbar)

In [95]:
df_kbar = {}

for sector, symbols in tokensDict.items() : 

    df_kbar[sector] = {}

    for symbol in symbols : 
        print("Now Downloading : " + symbol)
        
        try : 
            df_kbar[sector][symbol] = get_klines_data_from_binance(symbol= symbol + "USDT", 
                                                                   resample_freq ='4h', 
                                                                   start_time = datetime(2020,1,1), 
                                                                   end_time = datetime(2024,12,31), 
                                                                   futures=False)
        except : 
            pass

np.save('sectorKbar.npy', df_kbar)

Now Downloading : AGIX
Fetching spot data...
Spot data return error, fetching futures data...


Now Downloading : AI
Fetching spot data...
Now Downloading : AR
Fetching spot data...
Now Downloading : ARKM
Fetching spot data...
Now Downloading : CTXC
Fetching spot data...
Now Downloading : FET
Fetching spot data...


In [3]:
df_kbar = np.load('sectorKbar.npy',allow_pickle='TRUE').item()

### Get OI & Funding Rate Data

In [16]:
def get_future_data(symbol : str , start_ts, end_ts , exchange = 'binance', interval = '1d', dataType = 'oi'):
    req = requests.get(f'http://192.168.1.140:8002/coinglass/data?exchange={exchange}&interval={interval}&type={dataType}&symbol={symbol}&start={str(start_ts)}&end={str(end_ts)}')
    return req.json()

In [17]:
def getOIFundingRateData(ticker, start_date, end_date, dataType = 'oi') : 


    start_ts = datetime.timestamp(start_date)
    end_ts = datetime.timestamp(end_date)


    coinGlassDict = get_future_data(symbol = ticker, 
                                    interval = '4h', 
                                    start_ts = start_ts, 
                                    end_ts = end_ts , 
                                    dataType = dataType)
    
    dfBars =  pd.DataFrame(coinGlassDict['data'])
    dfBars.columns = coinGlassDict['columns'][0:len(dfBars.columns)]

    dfBars['datetime'] = pd.to_datetime(dfBars['timestamp'], unit='s')
    dfBars = dfBars.sort_values(by = 'datetime')

    return dfBars

In [18]:
df_OI = {}
df_FR = {}

for date, symbols in tokensTop100.items() : 

    df_OI[date] = {}
    df_FR[date] = {}

    for symbol in symbols : 
        #print("Now Downloading : " + symbol)
        
        try : 
            df_OI[date][symbol] = getOIFundingRateData(ticker = symbol + "USDT", 
                                                         start_date = date - pd.DateOffset(months = 3),
                                                         end_date = date + pd.DateOffset(months = 3),
                                                         dataType = 'oi' )
        except : 

            print("No OI Data : " + symbol)
            pass
        
        try : 
         
            df_FR[date][symbol] = getOIFundingRateData(ticker = symbol + "USDT", 
                                                         start_date = date - pd.DateOffset(months = 3),
                                                         end_date = date + pd.DateOffset(months = 3),
                                                         dataType = 'fr' )
        except : 

            print("No FR Data : " + symbol)
            pass



No OI Data : BTC
No FR Data : BTC
No OI Data : ETH
No FR Data : ETH
No OI Data : XRP
No FR Data : XRP
No OI Data : USDT
No FR Data : USDT
No OI Data : BCH
No FR Data : BCH
No OI Data : LTC
No FR Data : LTC
No OI Data : EOS
No FR Data : EOS
No OI Data : BNB
No FR Data : BNB
No OI Data : BSV
No FR Data : BSV
No OI Data : XTZ
No FR Data : XTZ
No OI Data : XLM
No FR Data : XLM
No OI Data : TRX
No FR Data : TRX
No OI Data : ADA
No FR Data : ADA
No OI Data : LEO
No FR Data : LEO
No OI Data : ATOM
No FR Data : ATOM
No OI Data : XMR
No FR Data : XMR
No OI Data : HT
No FR Data : HT
No OI Data : LINK
No FR Data : LINK
No OI Data : NEO
No FR Data : NEO
No OI Data : MIN
No FR Data : MIN
No OI Data : ETC
No FR Data : ETC
No OI Data : USDC
No FR Data : USDC
No OI Data : HEDG
No FR Data : HEDG
No OI Data : MIOTA
No FR Data : MIOTA
No OI Data : MKR
No FR Data : MKR
No OI Data : CRO
No FR Data : CRO
No OI Data : DASH
No FR Data : DASH
No OI Data : ONT
No FR Data : ONT
No OI Data : VET
No FR Data : VET


In [6]:
df_OI = {}
df_FR = {}

for sector, symbols in tokensDict.items() : 

    df_OI[sector] = {}
    df_FR[sector] = {}

    for symbol in symbols : 
        #print("Now Downloading : " + symbol)
        
        try : 
            df_OI[sector][symbol] = getOIFundingRateData(ticker = symbol + "USDT", 
                                                         start_date = datetime(2020,1,1),
                                                         end_date = datetime(2024,12,31),
                                                         dataType = 'oi' )
        except : 

            print("No OI Data : " + symbol)
            pass
        
        try : 
         
            df_FR[sector][symbol] = getOIFundingRateData(ticker = symbol + "USDT", 
                                                         start_date = datetime(2020,1,1),
                                                         end_date = datetime(2024,12,31),
                                                         dataType = 'fr' )
        except : 

            print("No FR Data : " + symbol)
            pass



No OI Data : AI
No FR Data : AI
No OI Data : CTXC
No FR Data : CTXC
No OI Data : IQ
No FR Data : IQ
No OI Data : PHA
No FR Data : PHA
No OI Data : BURGER
No FR Data : BURGER
No OI Data : GHST
No FR Data : GHST
No OI Data : MBOX
No FR Data : MBOX
No OI Data : PDA
No FR Data : PDA
No OI Data : PIXEL
No FR Data : PIXEL
No OI Data : PORTAL
No FR Data : PORTAL
No OI Data : PYR
No FR Data : PYR
No OI Data : RONIN
No FR Data : RONIN
No OI Data : VOXEL
No FR Data : VOXEL
No OI Data : XAI
No FR Data : XAI


### 抓出特定區間

-  盤整 (低波動)：ATR/收盤價 < N%
-  帶量：Volume > Volume 30 Days MA
-  突破：收盤價突破布林通道 ?

In [7]:
import ta

def add_atr_column(df) : 

    df['atr'] = ta.volatility.AverageTrueRange(
        df.high,
        df.low,
        df.close,
        window=6,
        fillna=False
    ).average_true_range() # <- call function

    return df

def get_ma(df, ma_len) :
    return df['close'].rolling(ma_len).mean()

def get_ma_abs_diff(df, ma_len) :

    return abs((df['close'] - df['close'].rolling(ma_len).mean())/df['close'])

def get_vol_ma(df, ma_len) :
    return df['volume'].rolling(ma_len).mean()


In [9]:
def get_bumpy_cond(df_price, df_oi_data, df_fr_data):

    # 計算快慢線
    df_price['quick_ma'] = get_ma(df_price, 5*6)
    df_price['slow_ma'] = get_ma(df_price, 10*6)

    df_price['quick_ma_pct'] = get_ma_abs_diff(df_price, 5*6)
    df_price['slow_ma_pct'] = get_ma_abs_diff(df_price, 10*6)

    df_price['vol_ma'] = get_vol_ma(df_price, 30*6)

    df_price = df_price[df_price['open_time'].dt.year >= 2023].copy()

    # 計算接下來 N 根 K 棒的報酬率
    df_price['future_close'] = df_price['close'].shift(-6)
    df_price['future_return'] = (df_price['future_close'] - df_price['close'])/df_price['close']

    # 計算接下來 N 根 K 棒的平均交易量
    df_price['past_mean_vol'] = df_price['volume'].rolling(6).mean()
    df_price['future_mean_vol'] = df_price['volume'].sort_index(ascending=False).rolling(6).mean().sort_index()
    
    # 計算接下來 N 根 K 棒的平均 OI 
    df_oi_data['past_mean_oi'] = df_oi_data['close'].rolling(6).mean()
    df_oi_data['future_mean_oi'] = df_oi_data['close'].sort_index(ascending=False).rolling(6).mean().sort_index()

    # 計算接下來 N 根 K 棒的平均 FR 
    df_fr_data['past_mean_fr'] = df_fr_data['close'].rolling(6).mean()
    df_fr_data['future_mean_fr'] = df_fr_data['close'].sort_index(ascending=False).rolling(6).mean().sort_index()

    # 盤整量縮條件
    df_price = df_price.merge(df_oi_data[['datetime', 'past_mean_oi', 'future_mean_oi']], 
                                                        left_on = ['open_time'], 
                                                        right_on = ['datetime'])
    
    
    df_price = df_price.merge(df_fr_data[['datetime', 'past_mean_fr', 'future_mean_fr']], 
                                                        left_on = ['open_time'], 
                                                        right_on = ['datetime'])
    

    
    df_below_ma_threshold = df_price[(df_price['quick_ma_pct'] < 0.1) & (df_price['slow_ma_pct'] < 0.1) & (df_price['volume'] < df_price['vol_ma']*1.5)].copy()
    #df_below_ma_threshold = df_price[(df_price['quick_ma_pct'] < 0.1) & (df_price['slow_ma_pct'] < 0.1)].copy()

    
    df_below_ma_threshold['index'] = df_below_ma_threshold.index
    df_below_ma_threshold['index_diff'] = df_below_ma_threshold['index'].diff()

    return df_below_ma_threshold


In [10]:
def add_bumpy_shaded_data(fig, df_price, df_oi_data, df_fr_data) : 
    
    df_below_ma_threshold = get_bumpy_cond(df_price, df_oi_data, df_fr_data)
    
    start_index = 0
    end_index = 0

    for i in range(1, len(df_below_ma_threshold)) :

        past_row = df_below_ma_threshold.iloc[i-1]
        current_row = df_below_ma_threshold.iloc[i]
        
        index_diff = current_row['index_diff']
        
        if index_diff > 1 :
            end_index = i-1

            start_time = df_below_ma_threshold['open_time'].iloc[start_index]
            end_time = df_below_ma_threshold['open_time'].iloc[end_index]
            
            future_return= df_below_ma_threshold['future_return'].iloc[end_index]
            past_mean_vol = df_below_ma_threshold['past_mean_vol'].iloc[end_index]
            future_mean_vol = df_below_ma_threshold['future_mean_vol'].iloc[end_index]
            
            past_mean_oi = df_below_ma_threshold['past_mean_oi'].iloc[end_index]
            future_mean_oi = df_below_ma_threshold['future_mean_oi'].iloc[end_index]

            past_mean_fr = df_below_ma_threshold['past_mean_fr'].iloc[end_index]
            future_mean_fr = df_below_ma_threshold['future_mean_fr'].iloc[end_index]

            # start_price = df_below_ma_threshold['close'].iloc[start_index]
            # end_price = df_below_ma_threshold['close'].iloc[start_index]

            # interval_return = (end_price - start_price)/start_price

            if (end_index - start_index > 6) : 

                derivativeCond = (future_mean_oi > past_mean_oi*1.1) | (future_mean_fr > past_mean_fr*1.1)
                #derivativeCond = True
                
                if (future_return > 1/100) & (future_mean_vol > past_mean_vol*1.1) & (derivativeCond):
                    # add shaded region
                    fig.add_vrect(
                            x0=start_time,
                            x1=end_time + pd.DateOffset(hours = 4*6),
                            fillcolor="grey",
                            opacity=0.1,
                            line_width=1,
                        )

            start_index = i
            end_index = 0


    return df_price, fig

In [11]:
def get_bumpy_plot(df_kbar, df_oi, df_FR,sector , token):

    df_price = df_kbar[sector][token]
    df_oi_data = df_oi[sector][token]
    df_fr_data = df_FR[sector][token]

    # df_price = add_atr_column(df_price)
    
    df_price['quick_ma'] = get_ma(df_price, 5*6)
    df_price['slow_ma'] = get_ma(df_price, 10*6)

    df_price['quick_ma_pct'] = get_ma_abs_diff(df_price, 5*6)
    df_price['slow_ma_pct'] = get_ma_abs_diff(df_price, 10*6)

    df_price['vol_ma'] = get_vol_ma(df_price, 30*6)

    df_price = df_price[df_price['open_time'] >= pd.Timestamp(2023,10,1)].copy()

    fig = make_subplots(specs=[[{"secondary_y": True}]])
    fig.add_trace(go.Scatter(x = df_price['open_time'] , y = df_price['close'], name = 'close'), secondary_y=True)
    fig.add_trace(go.Bar(x = df_price['open_time'] , y = df_price['volume'], name = 'volume'), secondary_y=False)
    fig.add_trace(go.Bar(x = df_oi_data['datetime'] , y = df_oi_data['close'], name = 'OI'), secondary_y=False)
    fig.add_trace(go.Bar(x = df_fr_data['datetime'] , y = df_fr_data['close'], name = 'FR'), secondary_y=False)

    # fig.add_trace(go.Bar(x = df_price['open_time'] , y = df_price['taker_buy_volume'], name = 'buy_volume'), secondary_y=False)
    # fig.add_trace(go.Bar(x = df_price['open_time'] , y = df_price['taker_sell_volume'], name = 'sell_volume'), secondary_y=False)
    # fig.add_trace(go.Bar(x = df_price['open_time'] , y = df_price['taker_buy_volume'] - df_price['taker_sell_volume'], name = 'buy_sell_diff'), secondary_y=False)

    # fig.add_trace(go.Scatter(x = df_price['open_time'] , y = df_price['vol_ma'], name = 'rolling_mean_volume'), secondary_y=False)

    fig.add_trace(go.Scatter(x = df_price['open_time'] , y = df_price['quick_ma'] , name = '7_ma'), secondary_y=True, row=1, col=1)
    fig.add_trace(go.Scatter(x = df_price['open_time'] , y = df_price['slow_ma'], name = '14_ma'), secondary_y=True, row=1, col=1)


    # fig.add_trace(go.Scatter(x = df_test['open_time'] , y = df_test['quick_ma_pct'] , name = '7_ma_pct'), secondary_y=False, row=1, col=1)
    # fig.add_trace(go.Scatter(x = df_test['open_time'] , y = df_test['slow_ma_pct'], name = '14_ma_pct'), secondary_y=False, row=1, col=1)

    temp, fig = add_bumpy_shaded_data(fig, df_price, df_oi_data, df_fr_data)

    #ol_column = "Binance_" + token + "USDT"
    #fig.add_trace(go.Bar(x = df_test['open_time'] , y = df_test[ol_column], name = 'OI'), secondary_y=False)
    fig.update_layout(title = token)

    fig.show()

    return temp


### 畫出特定區間

In [208]:
# AI
tokens = ['AGIX', 'AR', 'ARKM', 'FET', 'GRT', 'LPT', 'MDT', 'NEAR', 'NFP', 'OCEAN', 'PHB', 'RNDR', 'THETA', 'WLD']
# tokens = ["AGIX"]

# GameFi
#tokens = ['ACE', 'APE', 'AXS', 'BEAMX', 'CHR', 'COMBO', 'DAR', 'ENJ', 'FLOW', 'GALA', 'GMT', 'HIGH', 'ILV', 'IMX', 'MAGIC', 'MANA', 'SAND', 'SLP', 'SUPER', 'TLM', 'YGG']


for token in tokens : 

    try : 
        temp = get_bumpy_plot(df_kbar, df_OI, df_FR, sector = "AI" , token = token)
    except :
        pass

### 計算帶量突破後報酬率

In [163]:
def get_bumpy_cond(df_price, df_oi_data, df_fr_data):

    # 計算快慢線
    df_price['quick_ma'] = get_ma(df_price, 5*6)
    df_price['slow_ma'] = get_ma(df_price, 10*6)

    df_price['quick_ma_pct'] = get_ma_abs_diff(df_price, 5*6)
    df_price['slow_ma_pct'] = get_ma_abs_diff(df_price, 10*6)

    df_price['vol_ma'] = get_vol_ma(df_price, 30*6)

    #df_price = df_price[df_price['open_time'].dt.year >= 2023].copy()

    # 計算接下來 N 根 K 棒的報酬率
    df_price['future_close'] = df_price['close'].shift(-6)
    df_price['future_return'] = (df_price['future_close'] - df_price['close'])/df_price['close']

    # 計算接下來 N 根 K 棒的平均交易量
    df_price['past_mean_vol'] = df_price['volume'].rolling(6).mean()
    df_price['future_mean_vol'] = df_price['volume'].sort_index(ascending=False).rolling(6).mean().sort_index()
    
    # 計算接下來 N 根 K 棒的平均 OI 
    df_oi_data['past_mean_oi'] = df_oi_data['close'].rolling(60).mean()
    df_oi_data['future_mean_oi'] = df_oi_data['close'].sort_index(ascending=False).rolling(6).mean().sort_index()

    #計算接下來 N 根 K 棒的平均 FR 
    df_fr_data['past_mean_fr'] = df_fr_data['close'].rolling(60).mean()
    df_fr_data['future_mean_fr'] = df_fr_data['close'].sort_index(ascending=False).rolling(6).mean().sort_index()

    #盤整量縮條件
    df_price = df_price.merge(df_oi_data[['datetime', 'past_mean_oi', 'future_mean_oi']], 
                                                        left_on = ['open_time'], 
                                                        right_on = ['datetime'])
    
    
    df_price = df_price.merge(df_fr_data[['datetime', 'past_mean_fr', 'future_mean_fr']], 
                                                        left_on = ['open_time'], 
                                                        right_on = ['datetime'])
    

    
    df_below_ma_threshold = df_price[(df_price['quick_ma_pct'] < 0.1) & (df_price['slow_ma_pct'] < 0.1) & (df_price['volume'] < df_price['vol_ma']*1.5)].copy()
    
    
    df_below_ma_threshold['index'] = df_below_ma_threshold.index
    df_below_ma_threshold['index_diff'] = df_below_ma_threshold['index'].diff()

    return df_below_ma_threshold


In [164]:
def get_bumpy_interval(df_kbar, df_OI, df_FR, sector , token, isFROIFilter = True , returnLen = 5*6*4) : 

    df_price = df_kbar[sector][token].copy()
    df_oi_data = df_OI[sector][token].copy()
    df_fr_data = df_FR[sector][token].copy()

    df_below_ma_threshold = get_bumpy_cond(df_price, df_oi_data, df_fr_data)
        
    bumpyInterval = pd.DataFrame()
    start_index = 0
    end_index = 0

    for i in range(1, len(df_below_ma_threshold)) :

        past_row = df_below_ma_threshold.iloc[i-1]
        current_row = df_below_ma_threshold.iloc[i]
        
        index_diff = current_row['index_diff']
        
        if index_diff > 1 :
            end_index = i-1

            start_time = df_below_ma_threshold['open_time'].iloc[start_index]
            end_time = df_below_ma_threshold['open_time'].iloc[end_index]
            
            future_return= df_below_ma_threshold['future_return'].iloc[end_index]
            past_mean_vol = df_below_ma_threshold['past_mean_vol'].iloc[end_index]
            future_mean_vol = df_below_ma_threshold['future_mean_vol'].iloc[end_index]
            
            past_mean_oi = df_below_ma_threshold['past_mean_oi'].iloc[end_index]
            future_mean_oi = df_below_ma_threshold['future_mean_oi'].iloc[end_index]

            past_mean_fr = df_below_ma_threshold['past_mean_fr'].iloc[end_index]
            future_mean_fr = df_below_ma_threshold['future_mean_fr'].iloc[end_index]

            if (end_index - start_index > 6) :                

                if isFROIFilter : 

                    derivativeCond = (future_mean_oi > past_mean_oi*1.1) | (future_mean_fr > past_mean_fr*1.1)
                
                else : 
                    derivativeCond = True
                
                if (future_return > 0.5/100) & (future_mean_vol > past_mean_vol*1.1) & (derivativeCond):
                    
                    
                    startDate = df_below_ma_threshold['open_time'].iloc[start_index]
                    endDate = df_below_ma_threshold['open_time'].iloc[end_index]

                    bumpyEndClose = df_price[(df_price['open_time'] == endDate  + pd.DateOffset(hours = 4*6))]['close'].values[0]
                    afterSignalHours = 4

                    while afterSignalHours <= returnLen :

                        afterBumpyEndClose = df_price[(df_price['open_time'] == endDate + pd.DateOffset(hours = afterSignalHours) + pd.DateOffset(hours = 4*6))]['close'].values[0]
                        futureReturn = (afterBumpyEndClose - bumpyEndClose)/bumpyEndClose

                        if futureReturn <= -0.1 :
                            break
                        
                        afterSignalHours = afterSignalHours + 4



                    bumpyIntervalRow = { 
                                         'startDate' : [startDate],
                                         'endDate' : [endDate],
                                         'token' : [token],
                                         'futureReturn' : [futureReturn]

                                        }
                    



                    bumpyIntervalRow = pd.DataFrame(bumpyIntervalRow)
                    bumpyInterval = pd.concat([bumpyInterval, bumpyIntervalRow], ignore_index=True)

            start_index = i
            end_index = 0


    return bumpyInterval

In [140]:
def get_OIFR_interval(df_kbar, df_OI, df_FR, sector , token, returnLen = 5*6*4) : 

    df_price = df_kbar[sector][token].copy()
    df_oi_data = df_OI[sector][token].copy()
    df_fr_data = df_FR[sector][token].copy()

    df_below_ma_threshold = get_bumpy_cond(df_price, df_oi_data, df_fr_data)
        
    OIFRInterval = pd.DataFrame()

    for i in range(0, len(df_below_ma_threshold)) :

        past_mean_oi = df_below_ma_threshold['past_mean_oi'].iloc[i]
        future_mean_oi = df_below_ma_threshold['future_mean_oi'].iloc[i]

        past_mean_fr = df_below_ma_threshold['past_mean_fr'].iloc[i]
        future_mean_fr = df_below_ma_threshold['future_mean_fr'].iloc[i]

        
        derivativeCond = (future_mean_oi > past_mean_oi*1.1) | (future_mean_fr > past_mean_fr*1.1)
            
            
        if derivativeCond :
            
            startDate = df_below_ma_threshold['open_time'].iloc[i]
            endDate = df_below_ma_threshold['open_time'].iloc[i]

            bumpyEndClose = df_price[(df_price['open_time'] == endDate  + pd.DateOffset(hours = 4*6))]['close'].values[0]
            afterSignalHours = 4

            while afterSignalHours <= returnLen :

                afterBumpyEndClose = df_price[(df_price['open_time'] == endDate + pd.DateOffset(hours = afterSignalHours) + pd.DateOffset(hours = 4*6))]['close'].values[0]
                futureReturn = (afterBumpyEndClose - bumpyEndClose)/bumpyEndClose

                if futureReturn <= -0.1 :
                    break
                
                afterSignalHours = afterSignalHours + 4



            OIFRIntervalRow = { 
                                    'startDate' : [startDate],
                                    'endDate' : [endDate],
                                    'token' : [token],
                                    'futureReturn' : [futureReturn]

                                }
            



            OIFRIntervalRow = pd.DataFrame(OIFRIntervalRow)
            OIFRInterval = pd.concat([OIFRInterval, OIFRIntervalRow], ignore_index=True)

    return OIFRInterval

In [ ]:
# def get_bumpy_interval(df_kbar, sector , token, returnLen = 5*6*4) : 


#     df = df_kbar[sector][token]
    
#     df['quick_ma'] = get_ma(df, 5*6)
#     df['slow_ma'] = get_ma(df, 10*6)

#     df['quick_ma_pct'] = get_ma_abs_diff(df, 5*6)
#     df['slow_ma_pct'] = get_ma_abs_diff(df, 10*6)

#     df['vol_ma'] = get_vol_ma(df, 30*6)

    
#     # 計算接下來 N 根 K 棒的報酬率
#     df['future_close'] = df['close'].shift(-6)
#     df['future_return'] = (df['future_close'] - df['close'])/df['close']

#     # 計算接下來 N 根 K 棒的平均交易量
#     df['past_mean_vol'] = df['volume'].rolling(6).mean()
#     df['future_mean_vol'] = df['volume'].sort_index(ascending=False).rolling(6).mean().sort_index()
    
#     # 盤整量縮條件
#     df_below_ma_threshold = df[(df['quick_ma_pct'] < 0.05) & (df['slow_ma_pct'] < 0.05) & (df['volume'] < df['vol_ma']*1.5)].copy()
#     df_below_ma_threshold['index'] = df_below_ma_threshold.index
#     df_below_ma_threshold['index_diff'] = df_below_ma_threshold['index'].diff()


#     bumpyInterval = pd.DataFrame()
#     start_index = 0
#     end_index = 0

#     for i in range(1, len(df_below_ma_threshold)) :

#         past_row = df_below_ma_threshold.iloc[i-1]
#         current_row = df_below_ma_threshold.iloc[i]
        
#         index_diff = current_row['index_diff']
        
#         if index_diff > 1 :
#             end_index = i-1

#             start_time = df_below_ma_threshold['open_time'].iloc[start_index]
#             end_time = df_below_ma_threshold['open_time'].iloc[end_index]
            
#             future_return= df_below_ma_threshold['future_return'].iloc[end_index]
#             past_mean_vol = df_below_ma_threshold['past_mean_vol'].iloc[end_index]
#             future_mean_vol = df_below_ma_threshold['future_mean_vol'].iloc[end_index]

#             if (end_index - start_index > 6) : 
                

#                 if (future_return > 0.5/100) & (future_mean_vol > past_mean_vol*1.5):
                    
#                     startDate = df_below_ma_threshold['open_time'].iloc[start_index]
#                     endDate = df_below_ma_threshold['open_time'].iloc[end_index]

#                     bumpyEndClose = df[(df['open_time'] == endDate  + pd.DateOffset(hours = 4*6))]['close'].values[0]
#                     afterBumpyEndClose = df[(df['open_time'] == endDate + pd.DateOffset(hours = returnLen))]['close'].values[0]
#                     futureReturn = (afterBumpyEndClose - bumpyEndClose)/bumpyEndClose



#                     bumpyIntervalRow = { 
#                                          'startDate' : [startDate],
#                                          'endDate' : [endDate],
#                                          'token' : [token],
#                                          'futureReturn' : [futureReturn]

#                                         }
                    



#                     bumpyIntervalRow = pd.DataFrame(bumpyIntervalRow)
#                     bumpyInterval = pd.concat([bumpyInterval, bumpyIntervalRow], ignore_index=True)

#             start_index = i
#             end_index = 0


#     return bumpyInterval

In [166]:
def calculateBumpyReturn(df_kbar,df_OI ,df_FR,  sector, tokens, isFROIFilter = True, returnLen = 5*6*4):

    bumpyIntervalAll = pd.DataFrame()

    for token in tokens : 

        try : 
            bumpyInterval = get_bumpy_interval(df_kbar, df_OI ,df_FR, 
                                                sector= sector, token = token, returnLen = returnLen,
                                                isFROIFilter = isFROIFilter)

            bumpyIntervalAll = pd.concat([bumpyIntervalAll, bumpyInterval], ignore_index=True)

        except :
            pass
    
    return bumpyIntervalAll

def calculateOIFRReturn(df_kbar,df_OI ,df_FR,  sector, tokens, returnLen = 5*6*4):

    OIFRIntervalAll = pd.DataFrame()

    for token in tokens : 

        try : 

            OIFRInterval= get_OIFR_interval(df_kbar, df_OI, df_FR, sector= sector , token = token, returnLen = returnLen)

            OIFRIntervalAll = pd.concat([OIFRIntervalAll, OIFRInterval], ignore_index=True)

        except :
            pass
    
    return OIFRIntervalAll



def getReturnTable(bumpyIntervalAll):

    yearlyGroup = bumpyIntervalAll.groupby(bumpyIntervalAll['endDate'].dt.year)['futureReturn']
    

    yearlyReturnAnalysis = yearlyGroup.agg(
                                    mean = 'mean',
                                    max = 'max',
                                    min = 'min',
                                    std = 'std',
                                    n_trade = 'size',

                                )

    yearlyReturnAnalysis = yearlyReturnAnalysis.reset_index()

    allReturnSeries = bumpyIntervalAll['futureReturn']
    
    allReturnAnalysisRow = {
        'endDate' : "All",
        'mean' : [np.mean(allReturnSeries)], 
        'max' : [max(allReturnSeries)],
        'min' : [min(allReturnSeries)],
        'std' : [np.std(allReturnSeries)],
        'n_trade' : [len(allReturnSeries)]

    }

    allReturnAnalysisRow = pd.DataFrame(allReturnAnalysisRow)
    yearlyReturnAnalysis = pd.concat([yearlyReturnAnalysis, allReturnAnalysisRow], ignore_index=True)
    
    return yearlyReturnAnalysis


In [39]:
def yearlyTokenGraph(bumpyIntervalAll):

    yearlyTokenGroup=  bumpyIntervalAll.groupby([ bumpyIntervalAll['endDate'].dt.year, bumpyIntervalAll['token']])

    yearlyReturnProperty = yearlyTokenGroup['futureReturn'].agg(return_mean = "mean", 
                                                                n_trade = "size", 
                                                                win_trade = lambda x : len(x[x>0]),
                                                                lose_trade = lambda x : len(x[x<0]),).reset_index()

    years = yearlyReturnProperty['endDate'].unique()
    returnFig = make_subplots(rows=len(years))

    for i in range(1,len(years)+1):

        year = years[i-1]
        yearCond = (yearlyReturnProperty['endDate'] == year)
        figData = yearlyReturnProperty[yearCond]

        returnFig.add_trace(go.Bar(x= figData['token'], y= figData['return_mean']), col= 1 , row = i)
        returnFig.add_annotation(xref="x domain",yref="y domain",x=0.5, y=1.2, showarrow=False,
                        text= str(year), row=i, col=1)

    returnFig.update_layout(
        autosize=False,
        width=800,
        height=1000,
    )


    tradeFig = make_subplots(rows=len(years))

    for i in range(1,len(years)+1):

        year = years[i-1]
        yearCond = (yearlyReturnProperty['endDate'] == year)
        figData = yearlyReturnProperty[yearCond]

        tradeFig.add_trace(go.Bar(x= figData['token'], y= figData['n_trade'], name = 'all', marker_color = 'blue'), col= 1 , row = i)
        tradeFig.add_trace(go.Bar(x= figData['token'], y= figData['win_trade'], name = 'win', marker_color = 'green'), col= 1 , row = i)
        tradeFig.add_trace(go.Bar(x= figData['token'], y= figData['lose_trade'], name = 'lose', marker_color = 'red'), col= 1 , row = i)

        tradeFig.add_annotation(xref="x domain",yref="y domain",x=0.5, y=1.2, showarrow=False,
                        text= str(year), row=i, col=1)

    tradeFig.update_layout(
            autosize=False,
            width=800,
            height=1000,
        )
    
    return returnFig, tradeFig

In [127]:
from multiprocessing import Pool
import multiprocessing
import pickle


def getFutureTimeIndex(kbarYear,returnLen):

    endPrice = []

    while len(endPrice) == 0 : 

        randomIndex = randrange(len(kbarYear))
        startRow = kbarYear.iloc[randomIndex]
        
        startTime = startRow['open_time']
        startPrice = startRow['close']

        endTime = startTime  + pd.DateOffset(hours = returnLen)
        endPrice = kbarYear[kbarYear['open_time'] == endTime]['close'].reset_index(drop=True)

    return startTime


def func(item: tuple):

    #for token, kbar in df_kbar_sector.items() : 

    #for i in range(0,len(countOfToken)):

        #row = countOfToken.iloc[i]

        #year = row['endDate']
        #token = row['token']
        #count = row['count']

        #kbar = df_kbar[sector][token]

    token, kbar = item
    print(token)

    returnLen = 5*6*4

    years = kbar['open_time'].dt.year.unique()

    randomReturnDf = pd.DataFrame()
    
    for year in tqdm(years): 
        kbarYear = kbar[kbar['open_time'].dt.year == year].reset_index(drop = True)
        
        if len(kbarYear) > 360 :
            for j in range(0,100) :


                startTime = getFutureTimeIndex(kbarYear,returnLen)

                afterSignalHours = 4

                while afterSignalHours <= returnLen : 
                    
                    endTime = startTime  + pd.DateOffset(hours = afterSignalHours)
                    
                    try :
                        startPrice = kbarYear[kbarYear['open_time'] == startTime]['close'].reset_index(drop=True)
                        endPrice = kbarYear[kbarYear['open_time'] == endTime]['close'].reset_index(drop=True)

                        startPrice = startPrice[0]
                        endPrice = endPrice[0]
                        
                        randomReturn = (endPrice - startPrice)/startPrice

                        if randomReturn <= -0.1 : 
                            break

                    except :
                        pass
                    
                    afterSignalHours = afterSignalHours + 4
                    
                    

                randomReturnRow = { 'year' : [year],
                                    'token' : [token],
                                    'randomReturn' : [randomReturn]
                }

                randomReturnRow = pd.DataFrame(randomReturnRow)
                randomReturnDf = pd.concat([randomReturnDf, randomReturnRow], ignore_index= True)

    return randomReturnDf

def randomBeta(df_kbar, sector, bumpyIntervalAll, returnLen = 5*6*4) : 
    
    randomReturnDf = pd.DataFrame()
    #countOfToken = bumpyIntervalAll.groupby([bumpyIntervalAll['token'], bumpyIntervalAll['endDate'].dt.year])[['token']].size().reset_index(name = 'count')
    df_kbar_sector = df_kbar[sector].items()

    cpus = multiprocessing.cpu_count()
    print(f"Start with {cpus} cpus")

    with Pool(processes=6) as pool:
        randomReturnDf_token = list(tqdm(pool.imap(func, df_kbar_sector)))
        #randomReturnDf_token = randomReturnDf_token[0]

    for i in range(0, len(randomReturnDf_token)) : 
        randomReturnDf = pd.concat([randomReturnDf, randomReturnDf_token[i]], ignore_index=True)
        
    return randomReturnDf
    

In [41]:
bumpyTradeAI = calculateBumpyReturn(df_kbar, df_OI, df_FR, 'AI', tokensAI, isFROIFilter = False, returnLen = 5*6*4)
bumpyTradeGameFi = calculateBumpyReturn(df_kbar, df_OI, df_FR, 'GameFi', tokensGameFi, isFROIFilter = False, returnLen = 5*6*4)

In [148]:
OIFRTradeAI = calculateOIFRReturn(df_kbar, df_OI, df_FR, 'AI', tokensAI , returnLen = 5*6*4)
OIFRTradeGameFi = calculateOIFRReturn(df_kbar, df_OI, df_FR, 'GameFi', tokensGameFi, returnLen = 5*6*4)

In [167]:
bumpyOIFRTradeAI = calculateBumpyReturn(df_kbar, df_OI, df_FR, 'AI', tokensAI, isFROIFilter = True, returnLen = 5*6*4)
bumpyOIFRTradeGameFi = calculateBumpyReturn(df_kbar, df_OI, df_FR, 'GameFi', tokensGameFi, isFROIFilter = True, returnLen = 5*6*4)

In [169]:
bumpyOIFRReturnTableAI = getReturnTable(bumpyOIFRTradeAI)
bumpyOIFRReturnTableGameFi = getReturnTable(bumpyOIFRTradeGameFi)

In [155]:
OIFRReturnTableAI = getReturnTable(OIFRTradeAI)
OIFRReturnTableGameFi = getReturnTable(OIFRTradeGameFi)

In [ ]:
bumpyReturnTableAI = getReturnTable(bumpyTradeAI)
bumpyReturnTableGameFi = getReturnTable(bumpyTradeGameFi)

In [175]:
bumpyReturnTableAI

endDate      mean       max       min       std  n_trade
0    2020  0.048198  0.520008 -0.144278  0.146233       45
1    2021  0.039597  0.684663 -0.212563  0.166864       84
2    2022 -0.021532  0.329716 -0.162066  0.107619      130
3    2023  0.013689  0.906261 -0.155152  0.139146      193
4    2024  0.067930  1.511111 -0.177090  0.266663       57
5     All  0.018094  1.511111 -0.212563  0.159040      509

In [173]:
OIFRReturnTableGameFi

endDate      mean       max       min       std  n_trade
0    2023  0.040213  0.494595 -0.148811  0.115133     1938
1    2024 -0.011043  0.859257 -0.218275  0.114925     2020
2     All  0.014054  0.859257 -0.218275  0.117817     3958

In [170]:
bumpyOIFRReturnTableAI

endDate      mean       max      min       std  n_trade
0    2023  0.042994  0.410591 -0.12932  0.127105       32
1    2024  0.087501  1.511111 -0.17709  0.345399       26
2     All  0.062946  1.511111 -0.17709  0.246064       58

In [171]:
bumpyOIFRReturnTableGameFi

endDate      mean       max       min       std  n_trade
0    2023  0.057856  0.486073 -0.146341  0.135188       52
1    2024  0.044011  0.859257 -0.195011  0.182671       53
2     All  0.050868  0.859257 -0.195011  0.159531      105

In [45]:
# startTime = pd.Timestamp(2023,10,1)
# endTime = pd.Timestamp(2024,4,1)
# signalCountDf = pd.DataFrame()


# def getSectorReturn(investStartDate, df_price):

#   investEndDate = investStartDate + pd.DateOffset(days = 5)
#   return_list = []

#   for key, priceDf in df_price.items():

#     startPriceRow = priceDf[(priceDf['open_time'] == investStartDate)]['close']
#     endPriceRow = priceDf[(priceDf['open_time'] == investEndDate)]['close']

#     if (len(startPriceRow) > 0) & (len(endPriceRow) > 0):
      
#       startPrice = startPriceRow.values[0]
#       endPrice = endPriceRow.values[0]
#       return_ = (endPrice - startPrice)/startPrice

#       return_list.append(return_)

#   sectorReturn = np.mean(return_list)
#   return sectorReturn



# while startTime <= endTime :

#     signalStartTime = startTime - pd.DateOffset(days = 15)
#     signalEndTime = startTime

#     signalRecord = bumpyTradeGameFi[(bumpyTradeGameFi['startDate'] >=  signalStartTime) & (bumpyTradeGameFi['startDate'] < signalEndTime)]
#     signalRecord = signalRecord.drop_duplicates(subset = ['token'])

#     sectorReturn = getSectorReturn(investStartDate = signalEndTime, df_price = df_kbar['GameFi'])

#     signalCountRow = { 'datetime' : [startTime],
#                        'n_signal' : [len(signalRecord)],
#                        'sectorReturn' : [sectorReturn]
#                      }

#     signalCountRow = pd.DataFrame(signalCountRow)
#     signalCountDf = pd.concat([signalCountDf, signalCountRow], ignore_index=True)

#     startTime = startTime + pd.DateOffset(days = 1)

In [62]:
# dfAI = pd.DataFrame()
# for key, df in df_OI['GameFi'].items():

#     df = df.assign(token = key)
#     dfAI = pd.concat([dfAI, df], ignore_index=True)

# dfAI['year'] = dfAI['datetime'].dt.year
# dfAI[['year', 'token']].drop_duplicates().groupby(['year']).size()

In [47]:
bumpyReturnTableAI

endDate      mean       max       min       std  n_trade
0    2020  0.048198  0.520008 -0.144278  0.146233       45
1    2021  0.039597  0.684663 -0.212563  0.166864       84
2    2022 -0.021532  0.329716 -0.162066  0.107619      130
3    2023  0.013689  0.906261 -0.155152  0.139146      193
4    2024  0.067930  1.511111 -0.177090  0.266663       57
5     All  0.018094  1.511111 -0.212563  0.159040      509

In [48]:
bumpyReturnTableGameFi

endDate      mean       max       min       std  n_trade
0    2020 -0.002868  0.460354 -0.142600  0.153815       25
1    2021  0.056264  1.494487 -0.213162  0.277577       80
2    2022 -0.034659  0.187384 -0.175000  0.074864      120
3    2023  0.015084  0.486073 -0.147033  0.106092      197
4    2024  0.038227  0.859257 -0.195011  0.185631       51
5     All  0.010976  1.494487 -0.213162  0.157347      473

In [49]:
returnFigAI, tradeFigAI = yearlyTokenGraph(bumpyTradeAI)
returnFigGameFi, tradeFigGameFi = yearlyTokenGraph(bumpyTradeGameFi)

In [52]:
returnFigGameFi

In [128]:
# 模擬 Beta 數值

betaValueAIDf = pd.DataFrame()
betaValueGameFiDf = pd.DataFrame()

betaValueAIAll = []
betaValueGameFiAll = []

day = 5
for i in tqdm(range(0,1)) : 

    betaValueAI = randomBeta(df_kbar, sector = 'AI' ,  bumpyIntervalAll = bumpyTradeAI, returnLen = day*6*4)
    betaValueGameFi = randomBeta(df_kbar, sector = 'GameFi' ,  bumpyIntervalAll = bumpyTradeGameFi, returnLen = day*6*4)

    betaYearlyValueAI = betaValueAI.groupby(['year'])[['randomReturn']].mean().reset_index()
    betaYearlyValueGameFi = betaValueGameFi.groupby(['year'])[['randomReturn']].mean().reset_index()

    betaMeanAI = betaValueAI['randomReturn'].mean()
    betaMeanGameFi = betaYearlyValueGameFi['randomReturn'].mean()


    betaValueAIDf = pd.concat([betaValueAIDf, betaYearlyValueAI], ignore_index=True)
    betaValueGameFiDf = pd.concat([betaValueGameFiDf, betaYearlyValueGameFi], ignore_index=True)

    betaValueAIAll.append(betaMeanAI)
    betaValueGameFiAll.append(betaMeanGameFi)

  0%|          | 0/1 [00:00<?, ?it/s]

Start with 8 cpus


AGIX

0it [00:00, ?it/s]

AI
ARARKM

...





100%|██████████| 3/3 [00:13<00:00,  4.53s/it]


SAND





100%|██████████| 1/1 [00:04<00:00,  4.11s/it]


SLP





100%|██████████| 4/4 [00:17<00:00,  4.48s/it]






100%|██████████| 4/4 [00:13<00:00,  3.35s/it]



100%|██████████| 4/4 [00:17<00:00,  4.39s/it]

100%|██████████| 5/5 [00:21<00:00,  4.27s/it]





100%|██████████| 4/4 [00:16<00:00,  4.06s/it]

100%|██████████| 5/5 [00:20<00:00,  4.14s/it]

21it [00:51,  2.45s/it]
100%|██████████| 1/1 [01:33<00:00, 93.76s/it]


In [72]:
bumpyReturnTableAI

endDate      mean       max       min       std  n_trade
0    2020  0.048198  0.520008 -0.144278  0.146233       45
1    2021  0.039597  0.684663 -0.212563  0.166864       84
2    2022 -0.021532  0.329716 -0.162066  0.107619      130
3    2023  0.013689  0.906261 -0.155152  0.139146      193
4    2024  0.067930  1.511111 -0.177090  0.266663       57
5     All  0.018094  1.511111 -0.212563  0.159040      509

In [130]:
betaValueAIDf.groupby(['year'])[['randomReturn']].mean().reset_index()

year  randomReturn
0  2020      0.032402
1  2021      0.024274
2  2022     -0.009738
3  2023      0.016290
4  2024      0.040307

In [132]:
bumpyReturnTableGameFi

endDate      mean       max       min       std  n_trade
0    2020 -0.002868  0.460354 -0.142600  0.153815       25
1    2021  0.056264  1.494487 -0.213162  0.277577       80
2    2022 -0.034659  0.187384 -0.175000  0.074864      120
3    2023  0.015084  0.486073 -0.147033  0.106092      197
4    2024  0.038227  0.859257 -0.195011  0.185631       51
5     All  0.010976  1.494487 -0.213162  0.157347      473

In [131]:
betaValueGameFiDf.groupby(['year'])[['randomReturn']].mean().reset_index()

year  randomReturn
0  2020      0.000934
1  2021      0.030028
2  2022     -0.017373
3  2023      0.005851
4  2024      0.015040

In [44]:
np.mean(betaValueGameFiAll)

0.03052222880487116

In [ ]:
betaValueAIDf['randomReturn'].mean()

0.02687678085624002

In [ ]:
betaValueGameFiDf.groupby(['year'])[['randomReturn']].mean().reset_index()

year  randomReturn
0  2020      0.012115
1  2021      0.047298
2  2022      0.013598
3  2023      0.016587
4  2024      0.045464

In [ ]:
betaValueGameFiDf['randomReturn'].mean()

0.0270124701383336

In [ ]:
np.mean(betaValueAIList)

0.025491984966709888

In [ ]:
days = [5,6,7,8,9,10]
aiDf = pd.DataFrame()
gameFiDf = pd.DataFrame()

for day in tqdm(days) : 

    bumpyTradeAI = calculateBumpyReturn(df_kbar, df_OI, df_FR, 'AI', tokensAI, returnLen = day*6*4)
    bumpyTradeGameFi = calculateBumpyReturn(df_kbar, df_OI, df_FR, 'GameFi', tokensGameFi, returnLen = day*6*4)

    betaValueAIList = []
    betaValueGameFiList = []

    
    for i in tqdm(range(0,50)) : 

        betaValueAI = randomBeta(df_kbar, sector = 'AI' ,  bumpyIntervalAll = bumpyTradeAI, returnLen = day*6*4)
        betaValueGameFi = randomBeta(df_kbar, sector = 'GameFi' ,  bumpyIntervalAll = bumpyTradeGameFi, returnLen = day*6*4)

        betaValueAIList.append(betaValueAI)
        betaValueGameFiList.append(betaValueGameFi)

    
    aiRow = { 'day' : [day],
      'true_mean' : [np.mean(bumpyTradeAI['futureReturn'])],
      'random_mean' : [np.mean(betaValueAIList)]
    }

    gameFiRow = { 'day' : [day],
      'true_mean' : [np.mean(bumpyTradeGameFi['futureReturn'])],
      'random_mean' : [np.mean(betaValueGameFiList)]
    }

    aiRow = pd.DataFrame(aiRow)
    gameFiRow = pd.DataFrame(gameFiRow)
    aiDf = pd.concat([aiDf, aiRow], ignore_index=True)
    gameFiDf = pd.concat([gameFiDf, gameFiRow], ignore_index=True)

100%|██████████| 6/6 [04:29<00:00, 45.00s/it]


In [ ]:
aiDf

day  true_mean  random_mean
0    5   0.076080     0.019144
1    6   0.098895     0.023324
2    7   0.113597     0.024322
3    8   0.130051     0.036549
4    9   0.140975     0.043122
5   10   0.169690     0.042743

In [ ]:
gameFiDf

day  true_mean  random_mean
0    5   0.070278     0.019703
1    6   0.089364     0.037497
2    7   0.086033     0.032484
3    8   0.083156     0.041793
4    9   0.074956     0.043018
5   10   0.079715     0.056363

In [ ]:
returnBoxPlotAI = go.Figure()
returnBoxPlotGameFi = go.Figure()

for day in tqdm(days) : 

    bumpyTradeAI = calculateBumpyReturn(df_kbar, 'AI', tokensAI, returnLen = day*6*4)
    bumpyTradeGameFi = calculateBumpyReturn(df_kbar, 'GameFi', tokensGameFi, returnLen = day*6*4)

    returnBoxPlotAI.add_trace(go.Box(y = bumpyTradeAI['futureReturn'], name = day))
    returnBoxPlotGameFi.add_trace(go.Box(y = bumpyTradeGameFi['futureReturn'], name = day))


100%|██████████| 6/6 [03:08<00:00, 31.49s/it]


In [ ]:
returnBoxPlotAI

In [ ]:
returnBoxPlotAI

### 計算板塊帶量突破次數 & 未來報酬

In [ ]:
tokens = [ "RNDR", "AR", "FET" , "ARKM" , "OCEAN", "WLD", "AI", "AGIX"]

returnDf = pd.DataFrame()

for token in tokens : 

    df_test = df_kbar[token + "USDT"]
    startPriceMonth = df_test.groupby([df_test['open_time'].dt.year, df_test['open_time'].dt.month]).head(1).reset_index(drop = True)
    endPriceMonth = df_test.groupby([df_test['open_time'].dt.year, df_test['open_time'].dt.month]).tail(1).reset_index(drop = True)

    monthSeries = startPriceMonth['open_time']
    monthReturn = (endPriceMonth['close'] - startPriceMonth['close'])/startPriceMonth['close']

    returnRow = {'date' : monthSeries, 
    'return' : monthReturn,
    'token' : token,

    }

    returnRow = pd.DataFrame(returnRow)
    returnDf = pd.concat([returnDf, returnRow], ignore_index= True)


In [ ]:
bumpyIntervalAll['year'] = bumpyIntervalAll['endDate'].dt.year
bumpyIntervalAll['month'] = bumpyIntervalAll['endDate'].dt.month
bumpyIntervalUnique = bumpyIntervalAll[['token', 'year', 'month']].drop_duplicates()

bumpyIntervalCount = bumpyIntervalUnique.groupby(['year' , 'month'])[['token']].count().reset_index()

In [ ]:
bumpyIntervalAll

startDate             endDate token  year  month
0  2022-11-23 08:00:00 2022-11-26 08:00:00  RNDR  2022     11
1  2022-12-01 00:00:00 2022-12-03 12:00:00  RNDR  2022     12
2  2022-12-11 00:00:00 2022-12-12 20:00:00  RNDR  2022     12
3  2022-12-26 00:00:00 2022-12-28 08:00:00  RNDR  2022     12
4  2022-12-30 08:00:00 2023-01-03 20:00:00  RNDR  2023      1
..                 ...                 ...   ...   ...    ...
60 2023-08-06 00:00:00 2023-08-13 16:00:00  AGIX  2023      8
61 2023-08-25 12:00:00 2023-08-29 08:00:00  AGIX  2023      8
62 2023-08-31 20:00:00 2023-09-02 04:00:00  AGIX  2023      9
63 2023-09-13 08:00:00 2023-10-01 08:00:00  AGIX  2023     10
64 2023-10-13 16:00:00 2023-10-16 00:00:00  AGIX  2023     10

[65 rows x 5 columns]

In [ ]:
bumpyIntervalAll.groupby(['year', 'month'])[['token']].count().reset_index()

year  month  token
0   2022     11      2
1   2022     12      7
2   2023      1      3
3   2023      2      2
4   2023      3      1
5   2023      4      5
6   2023      5      2
7   2023      6      1
8   2023      7      7
9   2023      8      8
10  2023      9      6
11  2023     10     10
12  2023     11      2
13  2023     12      9

In [ ]:
returnDf['dateNextMonth'] = returnDf['date'] + pd.DateOffset(months = 1)

returnDf['year'] = returnDf['dateNextMonth'].dt.year
returnDf['month'] = returnDf['dateNextMonth'].dt.month
nextMonthReturn= returnDf.groupby(['year', 'month'])['return'].mean().reset_index()
tokenNumber = returnDf[['year', 'month', 'token']].drop_duplicates().groupby(['year', 'month']).count().reset_index()
tokenNumber = tokenNumber.rename(columns={'token' : 'tokenCount'})

In [ ]:
bumpyIntervalUnique[(bumpyIntervalUnique['year'] == 2023) & (bumpyIntervalUnique['month'] == 12)]

token  year  month
15   RNDR  2023     12
26     AR  2023     12
40    FET  2023     12
54  OCEAN  2023     12
58    WLD  2023     12

In [ ]:
bumpyIntervalCount = bumpyIntervalCount.merge(nextMonthReturn, on = ['year', 'month'])
bumpyIntervalCount = bumpyIntervalCount.merge(tokenNumber, on = ['year', 'month'])
bumpyIntervalCount

year  month  token    return  tokenCount
0   2022     11      2  0.132304           4
1   2022     12      3 -0.169448           4
2   2023      1      2  0.018048           4
3   2023      2      2  1.595306           4
4   2023      3      1  0.123338           5
5   2023      4      4 -0.137646           5
6   2023      5      2  0.048867           5
7   2023      6      1 -0.047358           5
8   2023      7      4 -0.157189           5
9   2023      8      5 -0.088431           7
10  2023      9      5 -0.169461           7
11  2023     10      6  0.085019           7
12  2023     11      2  0.281254           7
13  2023     12      5  0.329139           7

In [ ]:
df_test = df_kbar["FET" + "USDT"]
bumpyIntervalAll = pd.DataFrame()

for i in range(0, len(bumpyInterval)) :
    
    row = bumpyInterval.iloc[i]
    
    startDate = row['startDate']
    endDate = row['endDate']

    dateCond = (df_test['open_time'] >= startDate) & (df_test['open_time'] <= endDate)
    previousdateCond =  (df_test['open_time'] >= startDate - (endDate - startDate)) & (df_test['open_time'] <= startDate)
    
    bumpyIntervalData = df_test[dateCond]
    beforeBumpyIntervalData = df_test[previousdateCond]

    imbalance = abs(bumpyIntervalData['taker_buy_volume'] + bumpyIntervalData['taker_sell_volume'] )
    sellImbalance = np.where(bumpyIntervalData['taker_buy_volume'] - bumpyIntervalData['taker_sell_volume'] > 0, 
                                0 , 
                                abs(bumpyIntervalData['taker_buy_volume'] - bumpyIntervalData['taker_sell_volume'] ))
    # sellImbalance =  abs(bumpyIntervalData['taker_buy_volume'] - bumpyIntervalData['taker_sell_volume'] )

    sellRatio = sum(sellImbalance)/sum(imbalance)



    previmbalance = abs(beforeBumpyIntervalData['taker_buy_volume'] + beforeBumpyIntervalData['taker_sell_volume'] )
    prevsellImbalance = np.where(beforeBumpyIntervalData['taker_buy_volume'] - beforeBumpyIntervalData['taker_sell_volume'] > 0, 
                                0 , 
                                abs(beforeBumpyIntervalData['taker_buy_volume'] - beforeBumpyIntervalData['taker_sell_volume'] ))
    # prevsellImbalance =  abs(beforeBumpyIntervalData['taker_buy_volume'] - beforeBumpyIntervalData['taker_sell_volume'] )

    prevsellRatio = sum(prevsellImbalance)/sum(previmbalance)

    vpinRatio = sellRatio/prevsellRatio

    try : 
    
      bumpyEndClose = df_test[(df_test['open_time'] == endDate  + pd.DateOffset(hours = 4*6))]['close'].values[0]
      afterBumpyEndClose = df_test[(df_test['open_time'] == endDate + pd.DateOffset(hours = 4*6*4))]['close'].values[0]

      futureReturn = (afterBumpyEndClose - bumpyEndClose)/bumpyEndClose

      bumpyIntervalRow = { 'startDate' : [startDate], 
                            'endDate' : [endDate], 
                            'vpinRatio' : [vpinRatio],
                            'futureReturn' : [futureReturn]
                          }
    except : 
      pass

    bumpyIntervalRow = pd.DataFrame(bumpyIntervalRow)
    bumpyIntervalAll = pd.concat([bumpyIntervalAll, bumpyIntervalRow], ignore_index=True)

In [ ]:
bumpyIntervalAll

startDate             endDate  vpinRatio  futureReturn
0  2022-11-23 08:00:00 2022-11-26 08:00:00   0.661593      0.004785
1  2022-12-01 00:00:00 2022-12-03 12:00:00   0.800294      0.094488
2  2022-12-11 00:00:00 2022-12-12 20:00:00   1.186547     -0.003293
3  2022-12-26 00:00:00 2022-12-28 08:00:00   0.846320     -0.044979
4  2022-12-30 08:00:00 2023-01-03 20:00:00   0.555591      0.410188
5  2023-04-06 00:00:00 2023-04-10 12:00:00   1.435761      0.095318
6  2023-05-14 16:00:00 2023-05-16 08:00:00   1.069647      0.067083
7  2023-06-30 16:00:00 2023-07-03 04:00:00   1.253390     -0.100126
8  2023-07-10 12:00:00 2023-07-13 12:00:00   1.096022     -0.057785
9  2023-08-10 12:00:00 2023-08-14 00:00:00   0.596619     -0.149309
10 2023-08-25 16:00:00 2023-08-29 08:00:00   1.430281      0.115562
11 2023-09-03 16:00:00 2023-09-07 00:00:00   0.932929     -0.049735
12 2023-09-28 04:00:00 2023-10-01 04:00:00   0.519062     -0.077250
13 2023-10-12 20:00:00 2023-10-16 00:00:00   1.039390     -0.033692
14 2023-11-03 20:00:00 2023-11-06 04:00:00   1.461109      0.007674
15 2023-12-09 08:00:00 2023-12-11 08:00:00   1.064617      0.330905
16 2023-12-20 20:00:00 2023-12-23 08:00:00   1.945250      0.033903